In [1]:
TOKEN = 'BQDiN0lWyFGMyNQN9EYLdiYH1koeEBfpQD2vQwPh1U_7EWTWmJYgsTcZkJD2KrPrlZCZpkfKKtJRz7Otb3ZV5UKgt1mpD9whYWRDY4u1mDC0HJYis8P_ZLNFNN0afusqqxK8isMirkkipoWoCP1Dhnr5tN4'
import json
import requests
from math import ceil

import pandas as pd
import matplotlib

%matplotlib inline
import matplotlib.pyplot as plt

### First, I want to know how many song I have in my library

In [429]:
url = "https://api.spotify.com/v1/me/tracks"
headers = {'Authorization': "Bearer {}".format(TOKEN)}
r = requests.get(url, headers=headers)
parsed = json.loads(r.text)

In [430]:
parsed

{'href': 'https://api.spotify.com/v1/me/tracks?offset=0&limit=20',
 'items': [{'added_at': '2020-06-16T14:23:10Z',
   'track': {'album': {'album_type': 'album',
     'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/01qO0VcjpvkpAyrnYuz4bu'},
       'href': 'https://api.spotify.com/v1/artists/01qO0VcjpvkpAyrnYuz4bu',
       'id': '01qO0VcjpvkpAyrnYuz4bu',
       'name': 'Koes Plus',
       'type': 'artist',
       'uri': 'spotify:artist:01qO0VcjpvkpAyrnYuz4bu'}],
     'available_markets': ['AD',
      'AE',
      'AR',
      'AT',
      'AU',
      'BE',
      'BG',
      'BH',
      'BO',
      'BR',
      'CA',
      'CH',
      'CL',
      'CO',
      'CR',
      'CY',
      'CZ',
      'DE',
      'DK',
      'DO',
      'DZ',
      'EC',
      'EE',
      'EG',
      'ES',
      'FI',
      'FR',
      'GB',
      'GR',
      'GT',
      'HK',
      'HN',
      'HU',
      'ID',
      'IE',
      'IL',
      'IN',
      'IS',
      'IT',
      'JO',
      '

In [431]:
count_songs = parsed["total"]
print ("Total number of songs: {}".format(count_songs))

Total number of songs: 6711


### After getting total number of song, we can do looping for gathering all of our song.<br>Looping is necessary because Spotify limit the number of songs gathered

In [432]:
all_songs = []
for i in range(int(ceil(count_songs/50.0))):
    offset = 50*i
    url = "https://api.spotify.com/v1/me/tracks?limit=50&offset={}".format(offset)
    headers = {'Authorization': "Bearer {}".format(TOKEN)}
    r = requests.get(url, headers=headers)
    parsed = json.loads(r.text)

    all_songs.extend(parsed["items"])
print ("Number of gathered songs: {}".format(len(all_songs)))

Number of gathered songs: 6711


In [433]:
all_songs

[{'added_at': '2020-06-16T14:23:10Z',
  'track': {'album': {'album_type': 'album',
    'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/01qO0VcjpvkpAyrnYuz4bu'},
      'href': 'https://api.spotify.com/v1/artists/01qO0VcjpvkpAyrnYuz4bu',
      'id': '01qO0VcjpvkpAyrnYuz4bu',
      'name': 'Koes Plus',
      'type': 'artist',
      'uri': 'spotify:artist:01qO0VcjpvkpAyrnYuz4bu'}],
    'available_markets': ['AD',
     'AE',
     'AR',
     'AT',
     'AU',
     'BE',
     'BG',
     'BH',
     'BO',
     'BR',
     'CA',
     'CH',
     'CL',
     'CO',
     'CR',
     'CY',
     'CZ',
     'DE',
     'DK',
     'DO',
     'DZ',
     'EC',
     'EE',
     'EG',
     'ES',
     'FI',
     'FR',
     'GB',
     'GR',
     'GT',
     'HK',
     'HN',
     'HU',
     'ID',
     'IE',
     'IL',
     'IN',
     'IS',
     'IT',
     'JO',
     'JP',
     'KW',
     'LB',
     'LI',
     'LT',
     'LU',
     'LV',
     'MA',
     'MC',
     'MT',
     'MX',
     'MY',

Turning our data into list and then into dataframe

In [434]:
# create empty lists where the results are going to be stored
artist_name = []
track_name = []
popularity = []
track_id = []

In [435]:
for i in range(len(all_songs)):
    artist_name.append(all_songs[i]['track']['artists'][0]['name'])
    track_name.append(all_songs[i]['track']['name'])
    track_id.append(all_songs[i]['track']['id'])
    popularity.append(all_songs[i]['track']['popularity'])

In [436]:
df_tracks = pd.DataFrame({'artist_name':artist_name,'track_name':track_name,'track_id':track_id,'popularity':popularity})
print(df_tracks.shape)
# check if everything is ok
df_tracks.head()

(6711, 4)


artist_name            track_name                track_id  popularity
0   Koes Plus            Anak Manja  23xDflyvmkfkKDm6TLTC6c          15
1   Koes Plus            Cinta Buta  2mA3rND8OfaweQmNzbCC6k          15
2   Koes Plus           Cinta Mulia  0sls6RZiAhwqUdZfieQaz9          19
3   Koes Plus  Cintamu Tlah Berlalu  0mwtB9IS4tWCHbgRUnQzbL          20
4   Koes Plus          Cobaan Hidup  3DnduT3dPwe9t9YIncUWjF          15

In [437]:
df_tracks.isna().sum()

artist_name    0
track_name     0
track_id       0
popularity     0
dtype: int64

In [438]:
df_tracks.to_csv(r'df_tracks.csv')

### To complete our data, I need audio features of the tracks, which is a different endpoint

In [439]:
rows = []

for i in range(0,len(df_tracks['track_id'])):
    url = "https://api.spotify.com/v1/audio-features?ids={}".format(df_tracks['track_id'][i])
    headers = {'Authorization': "Bearer {}".format(TOKEN)}
    r = requests.get(url, headers=headers)
    parsed = json.loads(r.text)
    rows.append(parsed)

In [440]:
rows[0]['audio_features'][0]

{'danceability': 0.797,
 'energy': 0.718,
 'key': 10,
 'loudness': -5.544,
 'mode': 1,
 'speechiness': 0.0286,
 'acousticness': 0.561,
 'instrumentalness': 2.68e-05,
 'liveness': 0.16,
 'valence': 0.955,
 'tempo': 114.094,
 'type': 'audio_features',
 'id': '23xDflyvmkfkKDm6TLTC6c',
 'uri': 'spotify:track:23xDflyvmkfkKDm6TLTC6c',
 'track_href': 'https://api.spotify.com/v1/tracks/23xDflyvmkfkKDm6TLTC6c',
 'analysis_url': 'https://api.spotify.com/v1/audio-analysis/23xDflyvmkfkKDm6TLTC6c',
 'duration_ms': 220298,
 'time_signature': 4}

In [441]:
df_audio_features = pd.DataFrame.from_dict(rows[0]['audio_features'],orient='columns') 
for i in range(1, len(rows)):
    df_audio_features = df_audio_features.append(pd.DataFrame.from_dict(rows[i]['audio_features'],orient='columns'), 
                                                 ignore_index=True)

In [442]:
df_audio_features.head()

danceability  energy  key  loudness  mode  speechiness  acousticness  \
0         0.797   0.718   10    -5.544     1       0.0286         0.561   
1         0.766   0.580    0    -8.993     1       0.0311         0.425   
2         0.823   0.569    0    -7.859     1       0.0402         0.176   
3         0.533   0.411    2    -9.421     1       0.0260         0.689   
4         0.558   0.506    2    -6.221     1       0.0258         0.304   

   instrumentalness  liveness  valence    tempo            type  \
0          0.000027     0.160    0.955  114.094  audio_features   
1          0.000431     0.221    0.781  139.936  audio_features   
2          0.000000     0.136    0.917  129.081  audio_features   
3          0.000030     0.272    0.461  142.849  audio_features   
4          0.005420     0.292    0.431  137.967  audio_features   

                       id                                   uri  \
0  23xDflyvmkfkKDm6TLTC6c  spotify:track:23xDflyvmkfkKDm6TLTC6c   
1  2mA3rND8OfaweQmNzbCC6k  spotify:track:2mA3rND8OfaweQmNzbCC6k   
2  0sls6RZiAhwqUdZfieQaz9  spotify:track:0sls6RZiAhwqUdZfieQaz9   
3  0mwtB9IS4tWCHbgRUnQzbL  spotify:track:0mwtB9IS4tWCHbgRUnQzbL   
4  3DnduT3dPwe9t9YIncUWjF  spotify:track:3DnduT3dPwe9t9YIncUWjF   

                                          track_href  \
0  https://api.spotify.com/v1/tracks/23xDflyvmkfk...   
1  https://api.spotify.com/v1/tracks/2mA3rND8Ofaw...   
2  https://api.spotify.com/v1/tracks/0sls6RZiAhwq...   
3  https://api.spotify.com/v1/tracks/0mwtB9IS4tWC...   
4  https://api.spotify.com/v1/tracks/3DnduT3dPwe9...   

                                        analysis_url  duration_ms  \
0  https://api.spotify.com/v1/audio-analysis/23xD...       220298   
1  https://api.spotify.com/v1/audio-analysis/2mA3...       163693   
2  https://api.spotify.com/v1/audio-analysis/0sls...       172678   
3  https://api.spotify.com/v1/audio-analysis/0mwt...       123493   
4  https://api.spotify.com/v1/audio-analysis/3Dnd...       185281   

   time_signature  
0               4  
1               4  
2               4  
3               4  
4               4

In [443]:
df_audio_features.shape

(6711, 18)

In [444]:
df_audio_features.to_csv(r'df_audio_features.csv')

In [445]:
df_audio_features.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6711 entries, 0 to 6710
Data columns (total 18 columns):
danceability        6711 non-null float64
energy              6711 non-null float64
key                 6711 non-null int64
loudness            6711 non-null float64
mode                6711 non-null int64
speechiness         6711 non-null float64
acousticness        6711 non-null float64
instrumentalness    6711 non-null float64
liveness            6711 non-null float64
valence             6711 non-null float64
tempo               6711 non-null float64
type                6711 non-null object
id                  6711 non-null object
uri                 6711 non-null object
track_href          6711 non-null object
analysis_url        6711 non-null object
duration_ms         6711 non-null int64
time_signature      6711 non-null int64
dtypes: float64(9), int64(4), object(5)
memory usage: 943.9+ KB


In [446]:
df_tracks.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6711 entries, 0 to 6710
Data columns (total 4 columns):
artist_name    6711 non-null object
track_name     6711 non-null object
track_id       6711 non-null object
popularity     6711 non-null int64
dtypes: int64(1), object(3)
memory usage: 209.8+ KB


In [447]:
columns_to_drop = ['analysis_url','track_href','type']
df_audio_features.drop(columns_to_drop, axis=1,inplace=True)

df_audio_features.rename(columns={'id': 'track_id'}, inplace=True)

df_audio_features.shape

(6711, 15)

After I get the audio features, I merge them with the tracks dataframe

In [448]:
# merge both dataframes 
df = pd.merge(df_tracks,df_audio_features,on='track_id',how='inner') 
print("Shape of the dataset:", df_audio_features.shape) 
df.head()

Shape of the dataset: (6711, 15)


artist_name            track_name                track_id  popularity  \
0   Koes Plus            Anak Manja  23xDflyvmkfkKDm6TLTC6c          15   
1   Koes Plus            Cinta Buta  2mA3rND8OfaweQmNzbCC6k          15   
2   Koes Plus           Cinta Mulia  0sls6RZiAhwqUdZfieQaz9          19   
3   Koes Plus  Cintamu Tlah Berlalu  0mwtB9IS4tWCHbgRUnQzbL          20   
4   Koes Plus          Cobaan Hidup  3DnduT3dPwe9t9YIncUWjF          15   

   danceability  energy  key  loudness  mode  speechiness  acousticness  \
0         0.797   0.718   10    -5.544     1       0.0286         0.561   
1         0.766   0.580    0    -8.993     1       0.0311         0.425   
2         0.823   0.569    0    -7.859     1       0.0402         0.176   
3         0.533   0.411    2    -9.421     1       0.0260         0.689   
4         0.558   0.506    2    -6.221     1       0.0258         0.304   

   instrumentalness  liveness  valence    tempo  \
0          0.000027     0.160    0.955  114.094   
1          0.000431     0.221    0.781  139.936   
2          0.000000     0.136    0.917  129.081   
3          0.000030     0.272    0.461  142.849   
4          0.005420     0.292    0.431  137.967   

                                    uri  duration_ms  time_signature  
0  spotify:track:23xDflyvmkfkKDm6TLTC6c       220298               4  
1  spotify:track:2mA3rND8OfaweQmNzbCC6k       163693               4  
2  spotify:track:0sls6RZiAhwqUdZfieQaz9       172678               4  
3  spotify:track:0mwtB9IS4tWCHbgRUnQzbL       123493               4  
4  spotify:track:3DnduT3dPwe9t9YIncUWjF       185281               4

In [449]:
df.to_csv('spotify_data.csv')

## Getting my top artist

User's top artists is beneficial for making target dataset and filtering user's library track

In [27]:
artist = []
for i in range(0,2):
    offset = 49 * i
    url = "https://api.spotify.com/v1/me/top/artists?time_range=short_term&limit=50&offset={}".format(offset)
    headers = {'Authorization': "Bearer {}".format(TOKEN)}
    r = requests.get(url, headers=headers)
    parsed = json.loads(r.text)
    artist.append(parsed)

In [28]:
artist[0]['items'][0]['id']

'3aboSJaljyYlTRXt7pEH0G'

In [29]:
artist_name = []
genres = []
artist_id = []

for i in range(0,len(artist[0]['items']) + len(artist[1]['items'])):
    if i < 50:
        artist_name.append(artist[0]['items'][i]['name'])
        genres.append(artist[0]['items'][i]['genres'])
        artist_id.append(artist[0]['items'][i]['id'])
    if i >= 50:
        artist_name.append(artist[1]['items'][i-50]['name'])
        genres.append(artist[1]['items'][i-50]['genres'])
        artist_id.append(artist[1]['items'][i-50]['id'])

In [30]:
df_artists = pd.DataFrame({'artist_name':artist_name, 'genres': genres, 'artist_id': artist_id})
print(df_artists.shape)
# check if everything is ok
df_artists.head()

(57, 3)


artist_name                                             genres  \
0              TURBO                                       [korean pop]   
1    Vampire Weekend  [baroque pop, indie pop, indie rock, modern ro...   
2         Yves Tumor  [art pop, chamber psych, chillwave, escape roo...   
3        The Strokes  [alternative rock, garage rock, modern rock, p...   
4  Car Seat Headrest  [alternative rock, anti-folk, art pop, indie p...   

                artist_id  
0  3aboSJaljyYlTRXt7pEH0G  
1  5BvJzeQpmsdsFp4HGUYUEx  
2  0qu422H5MOoQxGjd4IzHbS  
3  0epOFNiUfyON9EYx7Tpr6V  
4  5PbpKlxQE0Ktl5lcNABoFf

In [31]:
artist = []
for i in range(0,2):
    offset = 49 * i
    url = "https://api.spotify.com/v1/me/top/artists?time_range=medium_term&limit=50&offset={}".format(offset)
    headers = {'Authorization': "Bearer {}".format(TOKEN)}
    r = requests.get(url, headers=headers)
    parsed = json.loads(r.text)
    artist.append(parsed)

In [32]:
artist_name = []
genres = []
artist_id = []

for i in range(0,len(artist[0]['items']) + len(artist[1]['items'])):
    if i < 50:
        artist_name.append(artist[0]['items'][i]['name'])
        genres.append(artist[0]['items'][i]['genres'])
        artist_id.append(artist[0]['items'][i]['id'])
    if i >= 50:
        artist_name.append(artist[1]['items'][i-50]['name'])
        genres.append(artist[1]['items'][i-50]['genres'])
        artist_id.append(artist[1]['items'][i-50]['id'])

In [33]:
df_artists = df_artists.append(pd.DataFrame({'artist_name':artist_name, 'genres': genres, 'artist_id': artist_id}), ignore_index = True)

In [34]:
df_artists.shape

(157, 3)

In [35]:
artist = []
for i in range(0,2):
    offset = 49 * i
    url = "https://api.spotify.com/v1/me/top/artists?time_range=long_term&limit=50&offset={}".format(offset)
    headers = {'Authorization': "Bearer {}".format(TOKEN)}
    r = requests.get(url, headers=headers)
    parsed = json.loads(r.text)
    artist.append(parsed)

artist_name = []
genres = []
artist_id = []

for i in range(0,len(artist[0]['items']) + len(artist[1]['items'])):
    if i < 50:
        artist_name.append(artist[0]['items'][i]['name'])
        genres.append(artist[0]['items'][i]['genres'])
        artist_id.append(artist[0]['items'][i]['id'])
    if i >= 50:
        artist_name.append(artist[1]['items'][i-50]['name'])
        genres.append(artist[1]['items'][i-50]['genres'])
        artist_id.append(artist[1]['items'][i-50]['id'])

In [36]:
df_artists = df_artists.append(pd.DataFrame({'artist_name':artist_name, 'genres': genres, 'artist_id': artist_id}),
                               ignore_index = True)

In [37]:
df_artists.shape

(257, 3)

In [38]:
# counting duplicates
grouped = df_artists.groupby(['artist_name'], as_index=True).size()
grouped[grouped > 1].count()

72

In [39]:
# dropping duplicates
df_artists.drop_duplicates(subset=['artist_name'], inplace=True)
df_artists.shape

(158, 3)

In [40]:
df_artists.reset_index(inplace = True)

In [41]:
df_artists.drop(['index'], axis = 1, inplace = True)

In [42]:
df_artists

artist_name                                             genres  \
0                TURBO                                       [korean pop]   
1      Vampire Weekend  [baroque pop, indie pop, indie rock, modern ro...   
2           Yves Tumor  [art pop, chamber psych, chillwave, escape roo...   
3          The Strokes  [alternative rock, garage rock, modern rock, p...   
4    Car Seat Headrest  [alternative rock, anti-folk, art pop, indie p...   
..                 ...                                                ...   
153        Project Pop                                   [indonesian pop]   
154            MF DOOM  [alternative hip hop, east coast hip hop, hard...   
155          Daft Punk                            [electro, filter house]   
156            SCALLER                                 [indonesian indie]   
157     Parquet Courts  [alternative rock, brooklyn indie, denton tx i...   

                  artist_id  
0    3aboSJaljyYlTRXt7pEH0G  
1    5BvJzeQpmsdsFp4HGUYUEx  
2    0qu422H5MOoQxGjd4IzHbS  
3    0epOFNiUfyON9EYx7Tpr6V  
4    5PbpKlxQE0Ktl5lcNABoFf  
..                      ...  
153  2D3ztMHoKJOJs3HgQJPXf6  
154  2pAWfrd7WFF3XhVt9GooDL  
155  4tZwfgrHOc3mvqYlEYSvVi  
156  6IjWOreXe5zdIiRpDD4stM  
157  23NIwARd4vPbxt3wwNnJ6k  

[158 rows x 3 columns]

In [43]:
df_artists.isna().sum()

artist_name    0
genres         0
artist_id      0
dtype: int64

In [44]:
df_artists.to_csv('my_top_artists.csv')